In [12]:
import sklearn.manifold as sm
import pandas as pd
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly.graph_objs as go
import pickle
from build_SQL_database import *
import itertools
import concurrent.futures as cf

init_notebook_mode(connected=True)

In [14]:
conn = connect_to_database()
executor = conn.cursor()

In [34]:
sims = pd.read_csv("similarity_matrix.csv", index_col=0)
sims.index = list(map(str, sims.index))
sims = sims.drop([person for person in sims if person not in sims.index], axis='columns')
similarities = sims.values

In [36]:
for person in range(len(similarities)):
    for dist in range(len(similarities[person])):
        if similarities[person][dist] < 0:
            similarities[person][dist] = 0

In [37]:
def nameid_to_hover_text(nameid, executor):
    executor.execute("SELECT user_name, full_text FROM tweets WHERE id==?", (nameid,))
    return "%s \n %s" % executor.fetchone()

In [59]:
hover_texts = [
    row 
    for row
    in conn.execute(
        "SELECT user_name, full_text FROM tweets WHERE id IN (%s)" % ','.join('?'*len(sims.index)), sims.index
    )
]

In [62]:
uniques = list(map(lambda x: x[0], hover_texts))
names = dict(zip(uniques, range(len(uniques))))
groups = [names[name[0]] for name in hover_texts]

In [69]:
embedding = sm.TSNE(metric="precomputed", perplexity=50).fit_transform(similarities)

In [71]:
x_vals = [coord[0] for coord in embedding]
y_vals = [coord[1] for coord in embedding]

trace = go.Scattergl(
    x = x_vals,
    y = y_vals,
    hoverinfo = "text",
    marker = dict(
        color = groups,
        colorscale='Rainbow'
    ),
    text = hover_texts,
    textposition = "bottom center",
    mode = "markers"
)

iplot([trace])